# **Bitcoin price prediction - Final scores**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author: Corsi Danilo (1742375) - corsi.1742375@studenti.uniroma1.it


---


Description: display of final scores and making predictions on the test set with the models trained on the whole train / validation set.

# Global constants, dependencies, libraries and tools

In [1]:
# Main constants
LOCAL_RUNNING = False
SLOW_OPERATIONS = False # Decide whether or not to use operations that might slow down notebook execution
ROOT_DIR = "D:/Documents/Repository/BDC/project" if LOCAL_RUNNING else "/content/drive"

In [2]:
if not LOCAL_RUNNING:
    # Point Colaboratory to Google Drive
    from google.colab import drive

    # Define GDrive paths
    drive.mount(ROOT_DIR, force_remount=True)

    # Install Spark and related dependencies
    !pip install pyspark
    !pip install -U -q PyDrive -qq
    !apt install openjdk-8-jdk-headless -qq

Mounted at /content/drive
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 316.9/316.9 MB 4.5 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyspark: filename=pyspark-3.5.0-py2.py3-none-any.whl size=317425344 sha256=685b4ffd51c9e50fdbe2763296be2aaea5647485f3a65053f7306a9254331209
  Stored in directory: /root/.cache/pip/wheels/41/4e/10/c2cf2467f71c678cfc8a6b9ac9241e5e44a01940da8fbb17fc
Successfully built pyspark
The following additional packages will be installed:
  libxtst6 openjdk-8-jre-headless
Suggested packages:
  openjdk-8-demo openjdk-8-source libnss-mdns fonts-dejavu-extra fonts-nanum fonts-ipafont-gothic
  fonts-ipafont-mincho fonts-wqy-microhei fonts-wqy-zenhei fonts-indic
The following NEW packages will be installed:
  libxtst6 openjdk-8-jdk-headless openjdk-8-jre-headless
0 upgraded, 3 newly installed, 0 to remove and 19 not upgraded.
Need to get 39.7 MB of archives.
After this operation, 144 MB of additional disk space will be used.
Selecting pre

## Import my utilities

In [3]:
# Set main dir
MAIN_DIR = ROOT_DIR + "" if LOCAL_RUNNING else ROOT_DIR + "/MyDrive/BDC/project"

# Utilities dir
UTILITIES_DIR = MAIN_DIR + "/utilities"

# Import my utilities
import sys
sys.path.append(UTILITIES_DIR)

from imports import *

In [4]:
# Set main dir
MAIN_DIR = ROOT_DIR + "" if LOCAL_RUNNING else ROOT_DIR + "/MyDrive/BDC/project"

###################
# --- DATASET --- #
###################

# Datasets dirs
DATASET_OUTPUT_DIR = MAIN_DIR + "/datasets/output"

# Datasets names
DATASET_TEST_NAME = "bitcoin_blockchain_data_15min_test"

# Datasets paths
DATASET_TEST = DATASET_OUTPUT_DIR + "/" + DATASET_TEST_NAME + ".parquet"

####################
# --- FEATURES --- #
####################

# Features dir
FEATURES_DIR = MAIN_DIR + "/features"

# Features labels
FEATURES_LABEL = "features"
TARGET_LABEL = "next-market-price"

# Features names
ALL_FEATURES_NAME = "all_features"
MOST_REL_FEATURES_NAME = "most_rel_features"
LEAST_REL_FEATURES_NAME = "least_rel_features"

# Features paths
ALL_FEATURES = FEATURES_DIR + "/" + ALL_FEATURES_NAME + ".json"
MOST_REL_FEATURES = FEATURES_DIR + "/" + MOST_REL_FEATURES_NAME + ".json"
LEAST_REL_FEATURES = FEATURES_DIR + "/" + LEAST_REL_FEATURES_NAME + ".json"

##################
# --- MODELS --- #
##################

# Model names
LR_MODEL_NAME = "LinearRegression"
GLR_MODEL_NAME = "GeneralizedLinearRegression"
RF_MODEL_NAME = "RandomForestRegressor"
GBT_MODEL_NAME = "GradientBoostingTreeRegressor"

# Model dir
MODELS_DIR = MAIN_DIR + "/models"

# Model path
LR_MODEL = MODELS_DIR + "/" + LR_MODEL_NAME
GLR_MODEL = MODELS_DIR + "/" + GLR_MODEL_NAME
RF_MODEL = MODELS_DIR + "/" + RF_MODEL_NAME
GBT_MODEL = MODELS_DIR + "/" + GBT_MODEL_NAME

###################
# --- RESULTS --- #
###################

# splits names
BLOCK_SPLITS_NAME = "block_splits"
WALK_FORWARD_SPLITS_NAME = "walk_forward_splits"
SHORT_TERM_SPLITS_NAME = "single_split"

# Results dir
RESULTS_DIR = MAIN_DIR + "/results"
RESULTS_FINAL_DIR = RESULTS_DIR + "/final"

In [5]:
# Suppression of warnings for better reading
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

if LOCAL_RUNNING: pio.renderers.default='notebook' # To correctly export the notebook in html format

# Create the pyspark session

In [6]:
# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '12G').\
                set('spark.driver.memory', '12G').\
                set('spark.driver.maxResultSize', '109G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPricePrediction").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

# Loading dataset

In [7]:
# Load datasets into pyspark dataset objects
df = spark.read.load(DATASET_TEST,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

In [8]:
def dataset_info(dataset):
  # Print dataset
  dataset.show(3)

  # Get the number of rows
  num_rows = dataset.count()

  # Get the number of columns
  num_columns = len(dataset.columns)

  # Print the shape of the dataset
  print("Shape:", (num_rows, num_columns))

  # Print the schema of the dataset
  dataset.printSchema()

In [9]:
if SLOW_OPERATIONS:
  dataset_info(df)

+-------------------+------+------------------+------------------+--------------------+-------------------+-----------------+------------------+--------------------+------------------------+--------------------+------------------+--------------------+--------------------+------------------+--------------+--------------------------------+-------------------+------------------+------------------+------------------+------------------+------------------+------------------+------------------+
|          timestamp|    id|      market-price|    total-bitcoins|          market-cap|       trade-volume|      blocks-size|    avg-block-size|n-transactions-total|n-transactions-per-block|           hash-rate|        difficulty|      miners-revenue|transaction-fees-usd|n-unique-addresses|n-transactions|estimated-transaction-volume-usd|     rate-of-change|        sma-5-days|        sma-7-days|       sma-10-days|       sma-20-days|       sma-50-days|      sma-100-days| next-market-price|
+-------------

# Load train / validation data

In [10]:
# Load models results
splits_list = [BLOCK_SPLITS_NAME, WALK_FORWARD_SPLITS_NAME, SHORT_TERM_SPLITS_NAME]
models_list = [LR_MODEL_NAME, GLR_MODEL_NAME, RF_MODEL_NAME, GBT_MODEL_NAME]
train_valid_results = pd.DataFrame(columns=['Model', 'Type', 'Dataset', 'Splitting', 'Features', 'Parameters', 'RMSE', 'MSE', 'MAE', 'MAPE', 'R2', 'Adjusted_R2', 'Time'])
train_valid_accuracy = pd.DataFrame(columns=['Model', 'Features', 'Splitting', 'Accuracy (default)', 'Accuracy (validated)'])
for split in splits_list:
    for model in models_list:
        if split == BLOCK_SPLITS_NAME:
            train_valid_results = pd.concat([train_valid_results, pd.read_csv(RESULTS_DIR + "/" + split + "/" + model + "_rel.csv")], ignore_index=True)
            train_valid_accuracy = pd.concat([train_valid_accuracy, pd.read_csv(RESULTS_DIR + "/" + split + "/" + model + "_accuracy.csv")], ignore_index=True)
        elif split == WALK_FORWARD_SPLITS_NAME:
            train_valid_results = pd.concat([train_valid_results, pd.read_csv(RESULTS_DIR + "/" + split + "/" + model + "_rel.csv")], ignore_index=True)
            train_valid_accuracy = pd.concat([train_valid_accuracy, pd.read_csv(RESULTS_DIR + "/" + split + "/" + model + "_accuracy.csv")], ignore_index=True)
        elif split == SHORT_TERM_SPLITS_NAME:
            train_valid_results = pd.concat([train_valid_results, pd.read_csv(RESULTS_DIR + "/" + split + "/" + model + "_rel.csv")], ignore_index=True)
            train_valid_accuracy = pd.concat([train_valid_accuracy, pd.read_csv(RESULTS_DIR + "/" + split + "/" + model + "_accuracy.csv")], ignore_index=True)


In [11]:
train_valid_results

Model          Type Dataset            Splitting  \
0                LinearRegression  default_norm     NaN         block_splits   
1                LinearRegression     cross_val     NaN         block_splits   
2     GeneralizedLinearRegression  default_norm     NaN         block_splits   
3     GeneralizedLinearRegression     cross_val     NaN         block_splits   
4           RandomForestRegressor  default_norm     NaN         block_splits   
5           RandomForestRegressor     cross_val     NaN         block_splits   
6   GradientBoostingTreeRegressor  default_norm     NaN         block_splits   
7   GradientBoostingTreeRegressor     cross_val     NaN         block_splits   
8                LinearRegression  default_norm     NaN  walk_forward_splits   
9                LinearRegression     cross_val     NaN  walk_forward_splits   
10    GeneralizedLinearRegression  default_norm     NaN  walk_forward_splits   
11    GeneralizedLinearRegression     cross_val     NaN  walk_forward_splits   
12          RandomForestRegressor  default_norm     NaN  walk_forward_splits   
13          RandomForestRegressor     cross_val     NaN  walk_forward_splits   
14  GradientBoostingTreeRegressor  default_norm     NaN  walk_forward_splits   
15  GradientBoostingTreeRegressor     cross_val     NaN  walk_forward_splits   
16               LinearRegression  default_norm     NaN         single_split   
17               LinearRegression         final     NaN         single_split   
18    GeneralizedLinearRegression  default_norm     NaN         single_split   
19    GeneralizedLinearRegression         tuned     NaN         single_split   
20          RandomForestRegressor  default_norm     NaN         single_split   
21          RandomForestRegressor         tuned     NaN         single_split   
22  GradientBoostingTreeRegressor  default_norm   valid         single_split   
23  GradientBoostingTreeRegressor         tuned   valid         single_split   

        Features                   Parameters         RMSE           MSE  \
0   all_features              [100, 0.0, 0.0]  2072.023594  7.790525e+06   
1   all_features               [80, 0.2, 0.2]  1427.699508  3.315925e+06   
2   all_features                      [25, 0]  2072.023594  7.790525e+06   
3   all_features    [5, 0, 'gaussian', 'log']  2072.023594  7.790525e+06   
4   all_features                  [20, 5, 42]  4482.521557  4.098833e+07   
5   all_features                  [5, 10, 42]  4550.966202  4.146350e+07   
6   all_features             [20, 5, 0.1, 42]  4551.614570  4.207171e+07   
7   all_features             [5, 10, 0.5, 42]  4691.422804  4.676871e+07   
8   all_features              [100, 0.0, 0.0]  2547.856094  1.836015e+07   
9   all_features                [5, 0.0, 0.0]  2617.062951  1.709796e+07   
10  all_features                      [25, 0]  2547.856094  1.836015e+07   
11  all_features    [5, 0, 'gaussian', 'log']  2547.856094  1.836015e+07   
12  all_features                  [20, 5, 42]  5190.939166  4.457179e+07   
13  all_features                 [10, 10, 42]  4953.583887  4.163708e+07   
14  all_features             [20, 5, 0.1, 42]  5300.901669  4.946748e+07   
15  all_features              [5, 5, 0.7, 42]  5126.273302  4.620198e+07   
16  all_features              [100, 0.0, 0.0]  3160.659705  9.989770e+06   
17  all_features                [5, 0.0, 0.0]  3160.659705  9.989770e+06   
18  all_features                      [25, 0]  3160.659705  9.989770e+06   
19  all_features  [5, 0.2, 'gaussian', 'log']   747.648005  5.589775e+05   
20  all_features                  [20, 5, 42]  2621.347009  6.871460e+06   
21  all_features                 [20, 10, 42]  2661.364283  7.082860e+06   
22  all_features             [20, 5, 0.1, 42]  6048.787724  3.658783e+07   
23  all_features             [10, 3, 0.3, 42]  3221.790016  1.037993e+07   

            MAE      MAPE         R2  Adjusted_R2      Time  
0   1732.276249  0.048265   0.312367     0.311843  0.447698  
1 

In [12]:
train_valid_accuracy

Model      Features            Splitting  \
0                LinearRegression  all_features         block_splits   
1     GeneralizedLinearRegression  all_features         block_splits   
2           RandomForestRegressor  all_features         block_splits   
3   GradientBoostingTreeRegressor  all_features         block_splits   
4                LinearRegression  all_features  walk_forward_splits   
5     GeneralizedLinearRegression  all_features  walk_forward_splits   
6           RandomForestRegressor  all_features  walk_forward_splits   
7   GradientBoostingTreeRegressor  all_features  walk_forward_splits   
8                LinearRegression  all_features         single_split   
9     GeneralizedLinearRegression  all_features         single_split   
10          RandomForestRegressor  all_features         single_split   
11  GradientBoostingTreeRegressor  all_features         single_split   

    Accuracy (default)  Accuracy (validated)  
0            51.725714             53.600000  
1            51.725714             51.725714  
2            50.167619             49.710476  
3            48.060952             46.617143  
4            49.330000             49.134545  
5            49.330000             49.330000  
6            46.572727             47.256364  
7            46.468182             46.348182  
8            45.161290             45.161290  
9            45.161290             45.161290  
10           52.553763             51.780914  
11           50.470430             45.161290

In [58]:
default_mask = train_valid_results['Type'].str.contains('default_norm|default')
tuned_mask = train_valid_results['Type'].str.contains('final|tuned|cross_val')

default_results = train_valid_results[default_mask]
tuned_results = train_valid_results[tuned_mask]

In [73]:
default_results

Model          Type Dataset            Splitting  \
0                LinearRegression  default_norm     NaN         block_splits   
2     GeneralizedLinearRegression  default_norm     NaN         block_splits   
4           RandomForestRegressor  default_norm     NaN         block_splits   
6   GradientBoostingTreeRegressor  default_norm     NaN         block_splits   
8                LinearRegression  default_norm     NaN  walk_forward_splits   
10    GeneralizedLinearRegression  default_norm     NaN  walk_forward_splits   
12          RandomForestRegressor  default_norm     NaN  walk_forward_splits   
14  GradientBoostingTreeRegressor  default_norm     NaN  walk_forward_splits   
16               LinearRegression  default_norm     NaN         single_split   
18    GeneralizedLinearRegression  default_norm     NaN         single_split   
20          RandomForestRegressor  default_norm     NaN         single_split   
22  GradientBoostingTreeRegressor  default_norm   valid         single_split   

        Features        Parameters         RMSE           MSE          MAE  \
0   all_features   [100, 0.0, 0.0]  2072.023594  7.790525e+06  1732.276249   
2   all_features           [25, 0]  2072.023594  7.790525e+06  1732.276249   
4   all_features       [20, 5, 42]  4482.521557  4.098833e+07  3910.543627   
6   all_features  [20, 5, 0.1, 42]  4551.614570  4.207171e+07  3765.261928   
8   all_features   [100, 0.0, 0.0]  2547.856094  1.836015e+07  2145.693637   
10  all_features           [25, 0]  2547.856094  1.836015e+07  2145.693637   
12  all_features       [20, 5, 42]  5190.939166  4.457179e+07  4437.898290   
14  all_features  [20, 5, 0.1, 42]  5300.901669  4.946748e+07  4517.726197   
16  all_features   [100, 0.0, 0.0]  3160.659705  9.989770e+06  3084.615825   
18  all_features           [25, 0]  3160.659705  9.989770e+06  3084.615825   
20  all_features       [20, 5, 42]  2621.347009  6.871460e+06  2329.232566   
22  all_features  [20, 5, 0.1, 42]  6048.787724  3.658783e+07  5208.837798   

        MAPE         R2  Adjusted_R2      Time  
0   0.048265   0.312367     0.311843  0.447698  
2   0.048265   0.312367     0.311843  0.386158  
4   0.097395  -0.895308    -0.896753  1.058586  
6   0.089769  -0.946178    -0.947662  5.250799  
8   0.062408  -0.505045    -0.506250  0.447235  
10  0.062408  -0.505045    -0.506250  0.405391  
12  0.144396  -4.181290    -4.185439  0.916291  
14  0.144694  -3.509128    -3.512739  4.958321  
16  0.115801 -23.322588   -23.355335  0.528631  
18  0.115801 -23.322588   -23.355335  0.510492  
20  0.087780 -15.730285   -15.752810  1.866193  
22  0.196549 -88.082212   -88.202148  5.393372

In [74]:
tuned_results

Model       Type Dataset            Splitting  \
1                LinearRegression  cross_val     NaN         block_splits   
3     GeneralizedLinearRegression  cross_val     NaN         block_splits   
5           RandomForestRegressor  cross_val     NaN         block_splits   
7   GradientBoostingTreeRegressor  cross_val     NaN         block_splits   
9                LinearRegression  cross_val     NaN  walk_forward_splits   
11    GeneralizedLinearRegression  cross_val     NaN  walk_forward_splits   
13          RandomForestRegressor  cross_val     NaN  walk_forward_splits   
15  GradientBoostingTreeRegressor  cross_val     NaN  walk_forward_splits   
17               LinearRegression      final     NaN         single_split   
19    GeneralizedLinearRegression      tuned     NaN         single_split   
21          RandomForestRegressor      tuned     NaN         single_split   
23  GradientBoostingTreeRegressor      tuned   valid         single_split   

        Features                   Parameters         RMSE           MSE  \
1   all_features               [80, 0.2, 0.2]  1427.699508  3.315925e+06   
3   all_features    [5, 0, 'gaussian', 'log']  2072.023594  7.790525e+06   
5   all_features                  [5, 10, 42]  4550.966202  4.146350e+07   
7   all_features             [5, 10, 0.5, 42]  4691.422804  4.676871e+07   
9   all_features                [5, 0.0, 0.0]  2617.062951  1.709796e+07   
11  all_features    [5, 0, 'gaussian', 'log']  2547.856094  1.836015e+07   
13  all_features                 [10, 10, 42]  4953.583887  4.163708e+07   
15  all_features              [5, 5, 0.7, 42]  5126.273302  4.620198e+07   
17  all_features                [5, 0.0, 0.0]  3160.659705  9.989770e+06   
19  all_features  [5, 0.2, 'gaussian', 'log']   747.648005  5.589775e+05   
21  all_features                 [20, 10, 42]  2661.364283  7.082860e+06   
23  all_features             [10, 3, 0.3, 42]  3221.790016  1.037993e+07   

            MAE      MAPE         R2  Adjusted_R2      Time  
1   1267.752796  0.035428   0.500187     0.499805  0.514274  
3   1732.276249  0.048265   0.312367     0.311843  0.454500  
5   3874.564315  0.097066  -0.957613    -0.959106  1.417800  
7   3946.234383  0.093835  -1.104813    -1.106419  3.511147  
9   2281.635511  0.064379  -0.163743    -0.164674  0.367184  
11  2145.693637  0.062408  -0.505045    -0.506250  0.349310  
13  4210.687195  0.137342  -3.363083    -3.366577  1.792143  
15  4342.102519  0.141886  -3.203794    -3.207161  1.827308  
17  3084.615825  0.115801 -23.322588   -23.355335  0.525142  
19   692.752335  0.025865  -0.360970    -0.362803  0.418831  
21  2340.444766  0.088192 -16.244990   -16.268208  4.277210  
23  2861.755353  0.107702 -24.272533   -24.306558  2.060357

In [90]:
def results_bar_plot(dataset, title):
  fig = px.bar(
    x=dataset['Model'],
    y=dataset['RMSE'],
    color=dataset['Splitting'],
    barmode='group'
  )

  fig.update_yaxes(side="left", showticklabels=True)
  fig.update_layout(title=title)
  fig.update_layout(legend_title_text="Splitting methods")
  fig.update_yaxes(showticklabels=False)
  fig.update_xaxes(title_text="Models")
  fig.update_yaxes(title='RMSE')

  fig.show()

In [91]:
results_bar_plot(default_results, "RMSE value for each default model")

In [92]:
results_bar_plot(tuned_results, "RMSE value for each tuned model")

In [86]:
# def results_bar_plot(title):
#   from plotly.subplots import make_subplots

#   fig = make_subplots(rows=1, cols=2)

#   fig1 = px.bar(
#     x=default_results['Model'],
#     y=default_results['RMSE'],
#     color=default_results['Splitting'],
#     barmode='group'
#   )

#   fig2 = px.bar(
#     x=tuned_results['Model'],
#     y=tuned_results['RMSE'],
#     color=tuned_results['Splitting'],
#     barmode='group'
#   )

#   # fig1.update_yaxes(side="left", showticklabels=True)
#   # fig1.update_layout(title=title)
#   # fig1.update_layout(legend_title_text="Splitting methods")
#   # fig1.update_yaxes(showticklabels=False)
#   # fig1.update_xaxes(title_text="Models")
#   # fig1.update_yaxes(title='RMSE')

#   # fig2.update_yaxes(side="left", showticklabels=True)
#   # fig2.update_layout(title=title)
#   # fig2.update_layout(legend_title_text="Splitting methods")
#   # fig2.update_yaxes(showticklabels=False)
#   # fig2.update_xaxes(title_text="Models")
#   # fig2.update_yaxes(title='RMSE')

#   # Add the traces to the subplot
#   fig.add_trace(fig1.data[0], row=1, col=1)
#   fig.add_trace(fig2.data[0], row=1, col=2)

#   fig.show()

In [89]:
# results_bar_plot("RMSE value for each model")

In [53]:
def accuracy_bar_plot(dataset, accuracy, title):
  fig = px.bar(
    x=dataset['Model'],
    y=dataset[accuracy],
    color=dataset['Splitting'],
    barmode='group'
  )

  fig.update_yaxes(side="left", showticklabels=True)
  fig.update_layout(title=title)
  fig.update_layout(legend_title_text="Splitting methods")
  fig.update_yaxes(showticklabels=False)
  fig.update_xaxes(title_text="Models")
  fig.update_yaxes(title='Accuracy')

  fig.show()

In [54]:
accuracy_bar_plot(train_valid_accuracy, 'Accuracy (default)', "Accuracy value for each default model")

In [57]:
accuracy_bar_plot(train_valid_accuracy, 'Accuracy (validated)', "Accuracy value for each tuned model")

# Test models
For each model, predictions on the various mini-sets are made and the obtained results are compared.

The test set is divided into further mini-sets of 1 week, 15 days, 1 month and 3 months to see how the models' performance degrades as the time taken into account increases.

In [10]:
# Retrieve the last value of the timestamp column
first_timestamp = df.select(col("timestamp")).first()[0]

# Split the test set into mini-sets of 1 week, 15 days, 1 month, and 3 months
one_week_df = df.filter(col("timestamp") <= first_timestamp + relativedelta(weeks=1))
fifteen_days_df = df.filter(col("timestamp") <= first_timestamp + relativedelta(days=15))
one_month_df = df.filter(col("timestamp") <= first_timestamp + relativedelta(months=1))
three_months_df = df.filter(col("timestamp") <= first_timestamp + relativedelta(months=3))

In [ ]:
'''
Description: Evaluate final model by making predictions on the test set
Args:
    dataset: The dataSet which needs to be splited
    dataset_name: Name of selected dataset [one_week | fifteen_days | one_month | three_months]
    model: Trained model
    model_name: Model name selected
    features_normalization: Indicates whether features should be normalized (True) or not (False)
    features: Features to be used to make predictions
    features_name: Name of features used
    features_label: The column name of features
    target_label: The column name of target variable
Return:
    results_df: Results obtained from the evaluation
    predictions: Predictions obtained from the model
'''
def evaluate_final_model(dataset, dataset_name, model, model_name, features_normalization, features, features_name, features_label, target_label):
    # Select the type of features to be used
    dataset = utilities.select_features(dataset, features_normalization, features, features_label, target_label)

    # Make predictions
    predictions = model.transform(dataset).select(target_label, "market-price", "prediction", 'timestamp')

    # Compute validation error by several evaluators
    eval_res = utilities.model_evaluation(target_label, predictions)

    # Use dict to store each result
    results = {
        "Model": model_name,
        "Dataset": dataset_name,
        "Features": features_name,
        "RMSE": eval_res['rmse'],
        "MSE": eval_res['mse'],
        "MAE": eval_res['mae'],
        "MAPE": eval_res['mape'],
        "R2": eval_res['r2'],
        "Adjusted_R2": eval_res['adj_r2'],
    }

    # Transform dict to pandas dataset
    results_pd = pd.DataFrame(results, index=[0])

    return results_pd, predictions

In [ ]:
'''
Description: How good the models are at predicting whether the price will go up or down
Args:
    dataset: The dataset which needs to be splited
Return:
    accuracy: Return the percentage of correct predictions
'''
def model_accuracy(dataset):
    # Compute the number of total rows in the DataFrame.
    total_rows = dataset.count()

    # Create a column "correct_prediction" which is worth 1 if the prediction is correct, otherwise 0
    dataset = dataset.withColumn(
        "correct_prediction",
        (
            (col("market-price") < col("next-market-price")) & (col("market-price") < col("prediction"))
        ) | (
            (col("market-price") > col("next-market-price")) & (col("market-price") > col("prediction"))
        )
    )

    # Count the number of correct predictions
    correct_predictions = dataset.filter(col("correct_prediction")).count()

    # Compite percentage of correct predictions
    accuracy = (correct_predictions / total_rows) * 100

    return accuracy

In [ ]:
# Loading all the features
with open(ALL_FEATURES, "r") as f:
    ALL_FEATURES = json.load(f)
print(ALL_FEATURES)

['market-price', 'market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'estimated-transaction-volume-usd', 'sma-20-days', 'trade-volume', 'sma-100-days', 'n-unique-addresses', 'transaction-fees-usd', 'total-bitcoins', 'n-transactions-total', 'blocks-size', 'sma-50-days', 'hash-rate', 'difficulty', 'avg-block-size', 'n-transactions-per-block', 'n-transactions', 'rate-of-change']


In [ ]:
# Loading the most relevant features
with open(MOST_REL_FEATURES, "r") as f:
    MOST_REL_FEATURES = json.load(f)
print(MOST_REL_FEATURES)

['market-price', 'market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'estimated-transaction-volume-usd', 'sma-20-days', 'trade-volume']


In [ ]:
# Load models
lr = PipelineModel.load(LR_MODEL)
glr = PipelineModel.load(GLR_MODEL)
rf = PipelineModel.load(RF_MODEL)
gbt = PipelineModel.load(GBT_MODEL)

In [ ]:
# Test models
model_name_list = [LR_MODEL_NAME, GLR_MODEL_NAME, RF_MODEL_NAME, GBT_MODEL_NAME]
model_list = [lr, glr, rf, gbt]
dataset_list = [one_week_df, fifteen_days_df, one_month_df, three_months_df]
dataset_name_list = ["one_week", "fifteen_days", "one_month", "three_months"]
predictions_df = pd.DataFrame(columns=[TARGET_LABEL, "market-price", "prediction", 'timestamp'])
test_results = pd.DataFrame(columns=['Model', 'Dataset', 'Features', 'RMSE', 'MSE', 'MAE', 'MAPE', 'R2', 'Adjusted_R2'])
test_accuracy = pd.DataFrame(columns=['Model', 'Features', 'Dataset', 'Accuracy'])

# For each model makes predictions based on the dataset type
for i, model in enumerate(model_list):
    for j, dataset in enumerate(dataset_list):
        # Select the type of feature to be used based on the model
        if (model_name_list[i] == LR_MODEL_NAME) or (model_name_list[i] == GLR_MODEL_NAME):
          FEATURES_NORMALIZATION = True
          CHOSEN_FEATURES = ALL_FEATURES
          CHOSEN_FEATURES_LABEL = ALL_FEATURES_NAME
        elif (model_name_list[i] == RF_MODEL_NAME) or (model_name_list[i] == GBT_MODEL_NAME):
          FEATURES_NORMALIZATION = True
          CHOSEN_FEATURES = MOST_REL_FEATURES
          CHOSEN_FEATURES_LABEL = MOST_REL_FEATURES_NAME

        results, predictions = evaluate_final_model(dataset, dataset_name_list[j], model, model_name_list[i], FEATURES_NORMALIZATION, CHOSEN_FEATURES, CHOSEN_FEATURES_LABEL, FEATURES_LABEL, TARGET_LABEL)
        test_results = pd.concat([test_results, results], ignore_index=True)

        predictions = predictions.withColumn("Model", lit(model_name_list[i])).withColumn("Dataset", lit(dataset_name_list[j]))
        predictions_df = pd.concat([predictions_df, predictions.toPandas()], ignore_index=True)

        accuracy = model_accuracy(predictions)
        accuracy_data = {
            'Model': model_name_list[i],
            'Features': CHOSEN_FEATURES_LABEL,
            'Dataset': dataset_name_list[j],
            'Accuracy': accuracy
        }
        accuracy_data_df = pd.DataFrame(accuracy_data, index=['Model'])

        test_accuracy = pd.concat([test_accuracy, accuracy_data_df], ignore_index=True)

# Merge results and accuracy
merged_results = pd.merge(test_results, test_accuracy)
merged_results


Model       Dataset           Features  \
0                LinearRegression      one_week       all_features   
1                LinearRegression  fifteen_days       all_features   
2                LinearRegression     one_month       all_features   
3                LinearRegression  three_months       all_features   
4     GeneralizedLinearRegression      one_week       all_features   
5     GeneralizedLinearRegression  fifteen_days       all_features   
6     GeneralizedLinearRegression     one_month       all_features   
7     GeneralizedLinearRegression  three_months       all_features   
8           RandomForestRegressor      one_week  most_rel_features   
9           RandomForestRegressor  fifteen_days  most_rel_features   
10          RandomForestRegressor     one_month  most_rel_features   
11          RandomForestRegressor  three_months  most_rel_features   
12  GradientBoostingTreeRegressor      one_week  most_rel_features   
13  GradientBoostingTreeRegressor  fifteen_days  most_rel_features   
14  GradientBoostingTreeRegressor     one_month  most_rel_features   
15  GradientBoostingTreeRegressor  three_months  most_rel_features   

            RMSE           MSE           MAE      MAPE           R2  \
0    2075.417120  4.307356e+06   2064.415840  0.068261   -15.580477   
1    1965.349628  3.862599e+06   1954.557344  0.064241   -19.154427   
2    2075.560812  4.307953e+06   2056.452154  0.067826   -33.704671   
3    2203.487393  4.855357e+06   2180.969541  0.076785    -0.440778   
4    1498.384880  2.245157e+06   1486.327631  0.049127    -7.642373   
5    1369.520929  1.875588e+06   1354.541504  0.044517    -8.786517   
6    1397.858527  1.954008e+06   1379.043572  0.045472   -14.741403   
7    1101.557253  1.213428e+06   1004.050182  0.034406     0.639927   
8   12700.519484  1.613032e+08  12690.288032  0.420049  -619.910794   
9   12907.181269  1.665953e+08  12899.754965  0.424090  -868.267872   
10  12813.586955  1.641880e+08  12808.742283  0.422406 -1321.691139   
11  11140.087551  1.241016e+08  10987.793077  0.382950   -35.825889   
12  14071.747363  1.980141e+08  14062.513610  0.465502  -761.223437   
13  14278.693175  2.038811e+08  14271.980543  0.469226 -1062.818975   
14  14185.343889  2.012240e+08  14180.967861  0.467673 -1620.051232   
15  12495.599829  1.561400e+08  12360.018655  0.431310   -45.332982   

    Adjusted_R2   Accuracy  
0    -15.679762  57.206538  
1    -19.210567  46.703678  
2    -33.752939  56.646998  
3     -0.441431  56.521739  
4     -7.694124  57.206538  
5     -8.813778  46.703678  
6    -14.763297  56.646998  
7      0.639764  56.521739  
8   -623.628822  57.206538  
9   -870.689231  46.703678  
10 -1323.530765  56.646998  
11   -35.842577  56.521739  
12  -765.787649  57.206538  
13 -1065.782259  46.703678  
14 -1622.305824  56.646998  
15   -45.353978  56.521739

# Models comparison

In [ ]:
def show_results(predictions, model0_name, model0_predictions, model1_name, model1_predictions, model2_name, model2_predictions, model3_name, model3_predictions, title):
  trace1 = go.Scatter(
      x = predictions['timestamp'],
      y = predictions['next-market-price'].astype(float),
      mode = 'lines',
      name = 'Next Market price (usd)'
  )

  trace2 = go.Scatter(
      x = model0_predictions['timestamp'],
      y = model0_predictions['prediction'].astype(float),
      mode = 'lines',
      name = model0_name + ' predictions'
  )

  trace3 = go.Scatter(
      x = model1_predictions['timestamp'],
      y = model1_predictions['prediction'].astype(float),
      mode = 'lines',
      name = model1_name + ' predictions'
  )

  trace4 = go.Scatter(
      x = model2_predictions['timestamp'],
      y = model2_predictions['prediction'].astype(float),
      mode = 'lines',
      name = model2_name + ' predictions'
  )

  trace5 = go.Scatter(
      x = model3_predictions['timestamp'],
      y = model3_predictions['prediction'].astype(float),
      mode = 'lines',
      name = model3_name + ' predictions'
  )

  layout = dict(
      title=title + " predictions",
      xaxis=dict(
          rangeselector=dict(
              buttons=list([
                  # Change the count to desired amount of months.
                  dict(count=1,
                      label='1m',
                      step='month',
                      stepmode='backward'),
                  dict(count=6,
                      label='6m',
                      step='month',
                      stepmode='backward'),
                  dict(count=12,
                      label='1y',
                      step='month',
                      stepmode='backward'),
                  dict(count=36,
                      label='3y',
                      step='month',
                      stepmode='backward'),
                  dict(step='all')
              ])
          ),
          rangeslider=dict(
              visible = True
          ),
          type='date'
      )
  )

  data = [trace1,trace2,trace3,trace4,trace5]
  fig = dict(data=data, layout=layout)
  iplot(fig, filename = title + " predictions")

In [ ]:
# For each dataset type, it displays the predicitons of each model
for dataset_name in dataset_name_list:
    predictions_to_show = predictions_df[predictions_df['Dataset'] == dataset_name]

    model_0_predictions = predictions_to_show[predictions_to_show['Model'] == model_name_list[0]]
    model_1_predictions = predictions_to_show[predictions_to_show['Model'] == model_name_list[1]]
    model_2_predictions = predictions_to_show[predictions_to_show['Model'] == model_name_list[2]]
    model_3_predictions = predictions_to_show[predictions_to_show['Model'] == model_name_list[3]]

    show_results(predictions_to_show, model_name_list[0], model_0_predictions, model_name_list[1], model_1_predictions, model_name_list[2], model_2_predictions, model_name_list[3], model_3_predictions, dataset_name)

# Summary

In [ ]:
scatter_plot(test_results, "RMSE", "Model", "RMSE value for each model")

In [ ]:
adv_scatter_plot(test_results, "RMSE", "Model", "Dataset", "RMSE value for each model (and dataset type)")

Considering the RMSE in the final results, we can see how Random Foreset and Gradient Boosting Tree Regressor reconfirm themselves as the best models, considering a narrow timeframe (ranging from one week to a maximum of one month), whereas if we lengthen the timeframe, performance degrades.

In [ ]:
scatter_plot(test_accuracy, "Accuracy", "Model", "Accuracy for each model")

In [ ]:
adv_scatter_plot(test_accuracy, "Accuracy", "Model", "Dataset", "Accuracy for each model (and dataset type)")

We see the same thing again in the accuracy, where this time the Random Forest at one week gives very good results, while as the timeframe is lengthened this starts to decrease.

In [ ]:
# Saving final test results
test_results.to_csv(RESULTS_FINAL_DIR + "/final.csv", index=False)
test_accuracy.to_csv(RESULTS_FINAL_DIR + "/final_accuracy.csv", index=False)

In [ ]:
# Export notebook in html format (remember to save the notebook and change the model name)
if LOCAL_RUNNING:
    !jupyter nbconvert --to html 6-final-scores.ipynb --output 6-final-scores --output-dir='./exports'